### ODE solvers

#### The Lorenz 63 "butterfly" plot 
( https://en.wikipedia.org/wiki/Lorenz_system )

Lorenz 63 is a system of 3 equations devepoed by Ed Lorenz ( https://en.wikipedia.org/wiki/Edward_Norton_Lorenz ) in build 54 in the 1960's, with computhing help from Ellen Fetter ( https://en.wikipedia.org/wiki/Ellen_Fetter ). The system is famous for being a very simple demonstration of a "chaotic" system. 

A chaotic system is a system in which a very small change in the initial conditions can get amplified in an unpredictable way so that two "trajectories" that are initially close separate to become very different. In a chaotic system, after some time, the difference between two similar but slight different initial trajectories is not proportional to the initial difference. 

Lorenz defined a system of 3 hypothetical variables, $x,y,z$ that vary in time, $t$ in relation to one another according to the equations

$$\begin{align}
\frac{dx}{dt} & =  \sigma(x-y)  \\
\frac{dy}{dt} & =  x(\rho-z)-y  \\
\frac{dz}{dt} & = xy-\beta z
\end{align}$$

with parameters, $\sigma, \rho, \beta$, constant in time.

In [ ]:
# Lets write a function to evaluate the Lorenz 63 equations
def lorenz63( x, y, z, σ=10., ρ=28., β=8./3. ):
    """
    Function to evaluate the Lorenz 63 time derivative equation for a given current
    state and parameters.
    Arguments: 
    x, y, z: x,y,z values.
    σ, ρ, β: static parameters α, ρ and β.
    """
    dxdt=σ*(y-x)
    dydt=x*ρ-x*z-y
    dzdt=x*y-β*z
    return dxdt,dydt,dzdt
?lorenz63  

In [ ]:
x,y,z=1,1,1;
dxdt,dydt,dzdt=lorenz63( x, y, z )
print(dxdt,dydt,dzdt)

For given initial conditions, we can simulate the time evolution of the Lorenz 63 system using the same sort
of timestepping we looked at in Lecture 1.
$$
\phi^{n+1}=\phi^{n}+\Delta t f(\phi^{n})
$$
this is not a very accurate numerical scheme (it is called an Euler forward scheme), so we will look at other schemes later. For illustrating programming concepts here it is usable.

In the Lorenz 63 case $\phi$ will be our array of time evolving values $x,y$ and $z$, and the function $f()$ can be our ``lorenz63`` Python function we just looked at.

In [ ]:
# Lets try this
import numpy as np
x0,y0,z0=0.,1.,1.05; Δt=0.01 # Initial conditions and paramters (note we need a discrete timestep)
nsteps=10000;
x=np.zeros(nsteps+1);x[0]=x0
y=np.zeros(nsteps+1);y[0]=y0
z=np.zeros(nsteps+1);z[0]=z0
for i in range(nsteps):
        dxdt,dydt,dzdt=lorenz63( x[i], y[i], z[i] )
        x[i+1]=x[i]+dxdt*Δt
        y[i+1]=y[i]+dydt*Δt
        z[i+1]=z[i]+dzdt*Δt
        
import matplotlib.pyplot as plt
from mpl_toolkits import mplot3d
plt.figure(figsize=(8,6))
ax=plt.axes(projection='3d')
ax.scatter3D(x,y,z,s=0.5);

In [ ]:
plt.plot(x);

In [6]:
# We can go a bit further with functions by defining a "timestepping" function for the Euler forward scheme we are using
# and passing the time-derivative function as an argument to a generic stepper.
def euler_forward_stepper(f, u0,nt,dt, **params):
    """
    Function euler_forward_stepper steps forward for n steps a set of discrete ODE equations
    using an Euler forward scheme.
    Arguments:
    f: Function that returns time-derivative at current value of the state, u.
       f is expected to have each component of u as a separate argument, followed
       by keyword arguments for named parameters.
    u0: Initial values for the components of u
    nsteps: number of steps to take
    dt: time-step
    params: Dictionary of parameter settings, set using keywords.
    """
    # Set up initial state
    nf=len(u0)
    u=np.zeros( (nt+1,nf) )
    dudt=np.zeros( nf )
    for i in range(nf):
        u[0,i]=u0[i]
        
    # Step forward
    for n in range(nt):
        dudt=f(*u[n,:],**params)
        u[n+1,:]=u[n,:]+np.array(dudt)*dt
        
    # return result
    return u

In [7]:
# We can go a bit further with functions by defining a "timestepping" function for the Euler forward scheme we are using
# and passing the time-derivative function as an argument to a generic stepper.
def euler_forward_step2(f, u0,nt,dt, **params):
    """
    Function euler_forward_step2 steps forward for n steps a set of discrete ODE equations
    using an Euler forward scheme.  This version uses and average of the derivatives 
    between the two points in the integration
    Arguments:
    f: Function that returns time-derivative at current value of the state, u.
       f is expected to have each component of u as a separate argument, followed
       by keyword arguments for named parameters.
    u0: Initial values for the components of u
    nsteps: number of steps to take
    dt: time-step
    params: Dictionary of parameter settings, set using keywords.
    """
    # Set up initial state
    nf=len(u0)
    u=np.zeros( (nt+1,nf) )
    dudt=np.zeros( nf )
    for i in range(nf):
        u[0,i]=u0[i]
        
    # Step forward
    for n in range(nt):
        dudt=f(*u[n,:],**params)
        t=u[n,:]+np.array(dudt)*dt # Temporary calc
        dudt2 = f(*t,**params)
        u[n+1,:]=u[n,:]+(np.array(dudt)+np.array(dudt2))/2*dt
        
    # return result
    return u

In [22]:
# Test to show effect small change in initial conditions
nsteps=10000;
dt=0.01;
eps=1.e-6  # Try different values for change in initial condition
Times = dt*np.array(list(range(nsteps+1)))
u0=euler_forward_stepper(lorenz63, np.array([0.,1.,1.05]), nsteps, dt);
u1=euler_forward_stepper(lorenz63, np.array([0.+eps,1.,1.05]), nsteps, dt);

In [ ]:
# Plot to compare X coordinates
plt.figure(figsize=(8,6))
plt.plot(Times,u0[:,0],label='IC 0,1,1.05'); plt.plot(Times,u1[:,0],label='IC 0+eps,1,1.05')
plt.title('Change in initial conditions')
plt.legend();

In [25]:
# Now see what happens when integrator is changed
nsteps=10000;
dt=0.01;
u0n=euler_forward_stepper(lorenz63, np.array([0.,1.,1.05]), nsteps, dt);
u1n=euler_forward_step2(lorenz63, np.array([0.,1.,1.05]), nsteps, dt);
# Plot to compare X coordinates
plt.figure(figsize=(8,6))
plt.plot(Times, u0n[:,0],label='stepper'); plt.plot(Times,u1n[:,0],label='stepper2')
plt.legend()
plt.title('Change in integrator');

##### This plot demonstrates why computer weather forecasts get less accurate with time. Can you think why the plot shows this!

In [ ]:
# Make figure appear in separate windows (so we have copies to compare).  Cell needs to execuated twice on PC and Mac until MacOSX or QTAgg is displayed.
%matplotlib

In [26]:
from scipy.integrate import odeint
def dfdy(y,t):
    return lorenz63( y[0], y[1], y[2] )
ys0=odeint(dfdy, np.array([0., 1., 1.05]), np.array([*range(0,10000)])*0.01) #,rtol=1.e-12,atol=1.0001e-12)
ys1=odeint(dfdy, np.array([0., 1., 1.05]), np.array([*range(0,10000)])*0.01, rtol=1.e-12,atol=1.e-12)

plt.figure(figsize=(8,3))
plt.plot(ys0[:,0],label='Default')
plt.plot(ys1[:,0],label='a/rtol=1.e-12')
plt.legend();

In [40]:
# Lotka-Volterra
def lv(y,t,α=1.,β=0.1,γ=1.5,ϵ=0.75):
    u_prey=y[0]
    v_pred=y[1]
    dudt =  α*u_prey - β*u_prey*v_pred 
    dvdt = -γ*v_pred + ϵ*β*u_prey*v_pred
    return dudt, dvdt
ys=odeint(lv, np.array([10, 5]), np.linspace(0, 50, 1000) )
zs=odeint(lv, np.array([10, 5]), np.linspace(0, 50, 1000),atol=1e-6,rtol=1e-6 )
Xvals=np.linspace(0, 50, 1000)
plt.figure(figsize=(8,6))
plt.plot(Xvals, ys[:,0],label='Hare')
plt.plot(Xvals,ys[:,1],label='Lynx')
plt.plot(Xvals,zs[:,0],label='Hare (tol)')
plt.plot(Xvals,zs[:,1],label='Lynx (tol)')
plt.legend();

In [ ]:
# %matplotlib
plt.figure(figsize=(8,6))
plt.plot(ys[:,0]-zs[:,0])
plt.plot(ys[:,1]-zs[:,1])
plt.ylabel('Differences')

In [44]:
# Using parameters
#
# More efficient Lynx

# Named parameters are not possible at moment
# α, β, γ, ϵ
p=(1.,0.1,1.5,0.75)
ys=odeint(lv, np.array([10, 5]), np.linspace(0, 50, 1000), p)
plt.figure(figsize=(16, 12))
plt.plot(ys[:,0])
plt.plot(ys[:,1]);